In [125]:
import os
os.chdir('/root/DiffusionBasedRL') 

In [126]:
# Change This
from config.maze2d import base
config = base['diffusion']

In [130]:
from loguru import logger
import os
logger.info(os.getcwd())
import sys
logger.info(sys.executable)
sys.path.append(os.getcwd())


from diffuser.models.dit import LDiT_models

import diffuser.utils as utils


#-----------------------------------------------------------------------------#
#----------------------------------- setup -----------------------------------#
#-----------------------------------------------------------------------------#

class argsmaker:
    # Change this
    dataset: str = 'maze2d-umaze-v1' #maze2d-large-v1, maze2d-medium-v1, maze2d-umaze-v1
    def __init__(self, inputargs):
        for k, v in inputargs.items():
            setattr(self, k, v)
        # Change logbase, horizon and n_diffusion_steps
        self.logbase = f'logs_dif_UMAZE_1M' #logs_dit_1M, logs_dit_UMaze_1M, logs_dif_UMAZE_1M
        self.horizon: int = 128 #384 for large, 256 for medium, 128 for small 
        self.n_diffusion_steps: int = 64 # 256 for large, 256 for medium, 64 for small
        self.savepath = f'{self.logbase}/{self.dataset}/diffusion/H{self.horizon}_T{self.n_diffusion_steps}'

args = argsmaker(config)

2024-06-06 22:29:26.659 | INFO     | __main__:<module>:3 - /root/DiffusionBasedRL
2024-06-06 22:29:26.661 | INFO     | __main__:<module>:5 - /opt/conda/envs/diffuser/bin/python


In [131]:
args.logbase

'logs_dif_UMAZE_1M'

In [132]:
#-----------------------------------------------------------------------------#
#---------------------------------- dataset ----------------------------------#
#-----------------------------------------------------------------------------#

dataset_config = utils.Config(
    args.loader,
    savepath=(args.savepath, 'dataset_config.pkl'),
    env=args.dataset,
    horizon=args.horizon,
    normalizer=args.normalizer,
    preprocess_fns=args.preprocess_fns,
    use_padding=args.use_padding,
    max_path_length=args.max_path_length,
)

render_config = utils.Config(
    args.renderer,
    savepath=(args.savepath, 'render_config.pkl'),
    env=args.dataset,
)

dataset = dataset_config()
renderer = render_config()

observation_dim = dataset.observation_dim
action_dim = dataset.action_dim


[ utils/config ] Imported diffuser.datasets:GoalDataset

[utils/config ] Config: <class 'diffuser.datasets.sequence.GoalDataset'>
    env: maze2d-umaze-v1
    horizon: 128
    max_path_length: 40000
    normalizer: LimitsNormalizer
    preprocess_fns: ['maze2d_set_terminals']
    use_padding: False

[ utils/config ] Saved config to: logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64/dataset_config.pkl

[ utils/config ] Imported diffuser.utils:Maze2dRenderer

[utils/config ] Config: <class 'diffuser.utils.rendering.Maze2dRenderer'>
    env: maze2d-umaze-v1

[ utils/config ] Saved config to: logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64/render_config.pkl



load datafile: 100%|██████████| 8/8 [00:00<00:00, 27.27it/s]


[ utils/preprocessing ] Segmented maze2d-umaze-v1 | 1565 paths | min length: 96 | max length: 3993
[ datasets/buffer ] Finalized replay buffer | 1566 episodes
[ datasets/buffer ] Fields:
    actions: (1566, 40000, 2)
    infos/goal: (1566, 40000, 2)
    infos/qpos: (1566, 40000, 2)
    infos/qvel: (1566, 40000, 2)
    observations: (1566, 40000, 4)
    rewards: (1566, 40000, 1)
    terminals: (1566, 40000, 1)
    timeouts: (1566, 40000, 1)
    next_observations: (1566, 40000, 4)
    normed_observations: (1566, 40000, 4)
    normed_actions: (1566, 40000, 2)


In [133]:

#-----------------------------------------------------------------------------#
#------------------------------ model & trainer ------------------------------#
#-----------------------------------------------------------------------------#

diffusion_config = utils.Config(
    args.diffusion,
    savepath=(args.savepath, 'diffusion_config.pkl'),
    horizon=args.horizon,
    observation_dim=observation_dim,
    action_dim=action_dim,
    n_timesteps=args.n_diffusion_steps,
    loss_type=args.loss_type,
    clip_denoised=args.clip_denoised,
    predict_epsilon=args.predict_epsilon,
    ## loss weighting
    action_weight=args.action_weight,
    loss_weights=args.loss_weights,
    loss_discount=args.loss_discount,
    device=args.device,
)

trainer_config = utils.Config(
    utils.Trainer,
    savepath=(args.savepath, 'trainer_config.pkl'),
    train_batch_size=args.batch_size,
    train_lr=args.learning_rate,
    gradient_accumulate_every=args.gradient_accumulate_every,
    ema_decay=args.ema_decay,
    sample_freq=args.sample_freq,
    save_freq=args.save_freq,
    label_freq=int(args.n_train_steps // args.n_saves),
    save_parallel=args.save_parallel,
    results_folder=args.savepath,
    bucket=args.bucket,
    n_reference=args.n_reference,
    n_samples=args.n_samples)

[ utils/config ] Imported diffuser.models:GaussianDiffusion

[utils/config ] Config: <class 'diffuser.models.diffusion.GaussianDiffusion'>
    action_dim: 2
    action_weight: 1
    clip_denoised: True
    horizon: 128
    loss_discount: 1
    loss_type: l2
    loss_weights: None
    n_timesteps: 64
    observation_dim: 4
    predict_epsilon: False

[ utils/config ] Saved config to: logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64/diffusion_config.pkl


[utils/config ] Config: <class 'diffuser.utils.training.Trainer'>
    bucket: None
    ema_decay: 0.995
    gradient_accumulate_every: 2
    label_freq: 40000
    n_reference: 50
    n_samples: 10
    results_folder: logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64
    sample_freq: 1000
    save_freq: 1000
    save_parallel: False
    train_batch_size: 32
    train_lr: 0.0002

[ utils/config ] Saved config to: logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64/trainer_config.pkl



In [134]:
#-----------------------------------------------------------------------------#
#-------------------------------- instantiate --------------------------------#
#-----------------------------------------------------------------------------#

if 'DiT' in args.model:
    model = LDiT_models[args.model](
        in_channels = observation_dim + action_dim,
        max_in_len = args.horizon,
    )
    model = model.to(device=args.device)
else:
    model_config = utils.Config(
        args.model,
        savepath=(args.savepath, 'model_config.pkl'),
        horizon=args.horizon,
        transition_dim=observation_dim + action_dim,
        cond_dim=observation_dim,
        dim_mults=args.dim_mults,
        device=args.device,
    )
    model = model_config()


diffusion = diffusion_config(model)

trainer = trainer_config(diffusion, dataset, renderer)

[ utils/config ] Imported diffuser.models:TemporalUnet

[utils/config ] Config: <class 'diffuser.models.temporal.TemporalUnet'>
    cond_dim: 4
    dim_mults: (1, 4, 8)
    horizon: 128
    transition_dim: 6

[ utils/config ] Saved config to: logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64/model_config.pkl

[ models/temporal ] Channel dimensions: [(6, 16), (16, 64), (64, 128)]
[(6, 16), (16, 64), (64, 128)]


In [135]:
checkpoints = sorted([int(x.split('_')[1].split('.')[0]) for x in os.listdir(trainer.logdir) if x.endswith('.pt')])


In [136]:
from diffuser.guides.policies import Policy

In [137]:
trainer.logdir

'logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64'

In [138]:
print(checkpoints[-1])
trainer.load(checkpoints[-1])
diffusion = trainer.model
policy = Policy(diffusion, dataset.normalizer)


720000


In [139]:
from tqdm import tqdm
from os.path import join

In [140]:
N = 100
batch_size = 1

In [141]:
import diffuser.datasets as datasets
import numpy as np

In [142]:
env = datasets.load_environment(args.dataset)

In [143]:
isconditioned = True

scorelist = []
for i in tqdm(range(N)):
    observation = env.reset()

    if isconditioned:
        logger.info('Resetting target')
        env.set_target()

    ## set conditioning xy position to be the goal
    target = env._target
    cond = {
        diffusion.horizon - 1: np.array([*target, 0, 0]),
    }

    ## observations for rendering
    rollout = [observation.copy()]

    total_reward = 0
    for t in range(env.max_episode_steps):

        state = env.state_vector().copy()

        ## can replan if desired, but the open-loop plans are good enough for maze2d
        ## that we really only need to plan once
        if t == 0:
            cond[0] = observation

            action, samples = policy(cond, batch_size=batch_size)
            actions = samples.actions[0]
            sequence = samples.observations[0]
        # pdb.set_trace()

        # ####
        if t < len(sequence) - 1:
            next_waypoint = sequence[t+1]
        else:
            next_waypoint = sequence[-1].copy()
            next_waypoint[2:] = 0

        ## can use actions or define a simple controller based on state predictions
        action = next_waypoint[:2] - state[:2] + (next_waypoint[2:] - state[2:])

        next_observation, reward, terminal, _ = env.step(action)
        total_reward += reward
        score = env.get_normalized_score(total_reward)
        # logger.info(
        #     f't: {t} | r: {reward:.2f} |  R: {total_reward:.2f} | score: {score:.4f} | ref_max_score: {env.ref_max_score} | ref_min_score: {env.ref_min_score}'
        #     f'{action}'
        # )

        xy = next_observation[:2]
        goal = env.unwrapped._target
        # logger.info(f'maze | pos: {xy} | goal: {goal}')

        ## update rollout observations
        rollout.append(next_observation.copy())


        if terminal:
            break

        observation = next_observation
    scorelist.append((total_reward, score)) 

# Save scorelist as json
result = {
    'return': [item[0] for item in scorelist],
    'scores': [item[1]*100 for item in scorelist]
}

  0%|          | 0/100 [00:00<?, ?it/s]2024-06-06 22:30:02.932 | INFO     | __main__:<module>:8 - Resetting target



                                                                                                    
1 / 64 [                                                            ]   1% | 114.6 Hz
t : 63
                                                                                                    
                                                                                                    
2 / 64 [#                                                           ]   3% | 127.0 Hz
t : 62
                                                                                                    
                                                                                                    
3 / 64 [##                                                          ]   4% | 132.0 Hz
t : 61
                                                                                                    
                                                                                                    
4 / 64 [###  

  1%|          | 1/100 [00:00<00:49,  2.01it/s]2024-06-06 22:30:03.429 | INFO     | __main__:<module>:8 - Resetting target


                                                                                                    
                                                                                                    
58 / 64 [######################################################      ]  90% | 139.9 Hz
t : 6
                                                                                                    
                                                                                                    
59 / 64 [#######################################################     ]  92% | 139.9 Hz
t : 5
                                                                                                    
                                                                                                    
60 / 64 [########################################################    ]  93% | 139.9 Hz
t : 4
                                                                                                    
              

  2%|▏         | 2/100 [00:00<00:48,  2.03it/s]2024-06-06 22:30:03.919 | INFO     | __main__:<module>:8 - Resetting target


...

                                                                                                    
                                                                                                    
59 / 64 [#######################################################     ]  92% | 133.7 Hz
t : 5
                                                                                                    
                                                                                                    
60 / 64 [########################################################    ]  93% | 133.7 Hz
t : 4
                                                                                                    
                                                                                                    
61 / 64 [#########################################################   ]  95% | 133.8 Hz
t : 3
                                                                                                    
              

 99%|█████████▉| 99/100 [00:49<00:00,  1.97it/s]2024-06-06 22:30:52.349 | INFO     | __main__:<module>:8 - Resetting target


                                                                                                    
                                                                                                    
43 / 64 [########################################                    ]  67% | 129.3 Hz
t : 21
                                                                                                    
                                                                                                    
44 / 64 [#########################################                   ]  68% | 129.5 Hz
t : 20
                                                                                                    
                                                                                                    
45 / 64 [##########################################                  ]  70% | 129.7 Hz
t : 19
                                                                                                    
           

100%|██████████| 100/100 [00:49<00:00,  2.00it/s]

                                                                                                    
                                                                                                    
56 / 64 [####################################################        ]  87% | 134.1 Hz
t : 8
                                                                                                    
                                                                                                    
57 / 64 [#####################################################       ]  89% | 134.1 Hz
t : 7
                                                                                                    
                                                                                                    
58 / 64 [######################################################      ]  90% | 134.1 Hz
t : 6
                                                                                                    
              

In [144]:
def printmetrics():
    print(f"Loaded from: {args.savepath}")
    print(f"Diffuser model is: {args.model}, dataset is: {args.dataset}, last checkpoint is: {checkpoints[-1]}")
    print(f"Mean score: {np.mean(result['scores'])}, std: {np.std(result['scores'])}")

In [145]:
printmetrics()

Loaded from: logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64
Diffuser model is: models.TemporalUnet, dataset is: maze2d-umaze-v1, last checkpoint is: 720000
Mean score: 127.97623360626041, std: 28.764015496442944


In [112]:
printmetrics()

Loaded from: logs_dit_1M/maze2d-large-v1/diffusion/H384_T256
Diffuser model is: DiT-XXS, dataset is: maze2d-large-v1, last checkpoint is: 1320000
Mean score: 140.34569194507833, std: 51.24710856068407


In [90]:
printmetrics()

Loaded from: logs_dit_UMaze_1M/maze2d-umaze-v1/diffusion/H128_T64
Diffuser model is: DiT-XXS, dataset is: maze2d-umaze-v1, last checkpoint is: 1600000
Mean score: 129.96884283747553, std: 14.004032764304547


In [55]:
printmetrics()

Loaded from: logs_dif_UMAZE_1M/maze2d-umaze-v1/diffusion/H128_T64
Diffuser model is: models.TemporalUnet, dataset is: maze2d-umaze-v1, last checkpoint is: 680000
Mean score: 131.63538873994636, std: 16.61891977991106
